In [1]:
import os, sys
module_path = os.path.abspath(os.path.join('..'))
if module_path not in sys.path:
    sys.path.append(module_path)
from utils.helpers import launch_env, wrap_env, view_results_ipython, force_done
from utils.helpers import SteeringToWheelVelWrapper, ResizeWrapper, ImgWrapper

import numpy as np

import torch
import torch.nn as nn
from torch import optim

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

INFO:aido-protocols:aido-protocols 5.0.18
13:31:23|zj|__init__.py:4|<module>(): zuper-ipce 5.1.2
13:31:23|zuper-typing|__init__.py:5|<module>(): zuper-typing 5.0.12
13:31:23|zuper-commons|__init__.py:9|<module>(): zuper-commons 5.0.7
13:31:23|zuper-typing|zeneric2.py:48|<module>(): In Python 3.6
13:31:23|zuper-nodes|__init__.py:8|<module>(): zuper-nodes 5.0.9


# Generating Data from a Teacher

In order to use imitation learning in practice, we need to have _demonstrations_. However, demonstrations need to be gathered; in general, we can collect the demonstrations that we need in one of four ways:

* Human demonstrator teleoperating the robot
* Data logs or historical data
* Learned policy (i.e from reinforcement learning) is rolled out
* Hard-coded expert is rolled out

While these trajectories can be gathered on real robots, to speed up collection, we work mainly in simulation. Duckietown has a [vast](https://logs.duckietown.org) collection of logs gathered over years of running programs on Duckiebots, but here, we focus on the last data collection method: a hard-coded expert.

**<font color='red'>Question 1:</font> What are some pros and cons of each approach? List two pros and two cons for each of the four methods listed above.**

We first introduce a _pure-pursuit expert_ - often, in robotic imitation learning, we have controllers to control many of our robots and systems; a pure-pursuit expert is about the simplest controller that we can have for a Duckiebot.

Our expert drives with ground-truth state data; while more complicated controllers incorporate and fuse observational data to estimate a state, we use data that'd a robot would not normally have access to.

In [47]:
class PurePursuitExpert:
    def __init__(self, env, ref_velocity=0.2, position_threshold=0.8, gain=2,
                 following_distance=0.8, max_iterations=1000):
        self.env = env.unwrapped
        self.following_distance = following_distance
        self.max_iterations = max_iterations
        self.ref_velocity = ref_velocity
        self.gain = gain
        self.position_threshold = position_threshold

    def predict(self, observation):  
        # Our expert drives with "cheating" data, something your implementation will not have access to
        closest_point, closest_tangent = self.env.closest_curve_point(self.env.cur_pos, self.env.cur_angle)

        iterations = 0
        lookup_distance = self.following_distance
        curve_point = None
        while iterations < self.max_iterations:
            # Project a point ahead along the curve tangent,
            # then find the closest point to to that
            follow_point = closest_point + closest_tangent * lookup_distance
            curve_point, _ = self.env.closest_curve_point(follow_point, self.env.cur_angle)

            # If we have a valid point on the curve, stop
            if curve_point is not None:
                break

            iterations += 1
            lookup_distance *= 0.5

        # Compute a normalized vector to the curve point
        point_vec = curve_point - self.env.cur_pos
        point_vec /= np.linalg.norm(point_vec)

        dot = np.dot(self.env.get_right_vec(), point_vec)
        steering = self.gain * -dot

        return self.ref_velocity, steering

In [48]:
nsteps = 500

In [49]:
local_env = launch_env()
local_env = wrap_env(local_env)
local_env = ResizeWrapper(local_env)
local_env = ImgWrapper(local_env)

local_env.reset()
wrapper = SteeringToWheelVelWrapper()

# Create an demonstrator
expert = PurePursuitExpert(env=local_env)

observations = []
actions = []

# Collect samples

for steps in range(0, nsteps):
    # use our 'expert' to predict the next action.
    action = expert.predict(None)
    action = wrapper.convert(action)
    observation, reward, done, info = local_env.step(action)
    observations.append(observation)
    actions.append(action)

    if done:
        local_env.reset()
        
local_env.close()

print('\nDone!\n')

14:14:50|gym-duckietown|graphics.py:121|create_frame_buffers(): Falling back to non-multisampled frame buffer
14:14:50|gym-duckietown|graphics.py:121|create_frame_buffers(): Falling back to non-multisampled frame buffer
14:14:50|gym-duckietown|simulator.py:578|_load_map(): loading map file "/duckietown/simulation/src/gym_duckietown/maps/loop_empty.yaml"
14:14:50|gym-duckietown|simulator.py:1140|_drivable_pos(): [4.13719561 0.         1.88880899] corresponds to tile at (7, 3) which is not drivable: {'coords': (7, 3), 'kind': 'floor', 'angle': 0, 'drivable': False, 'texture': <simulation.src.gym_duckietown.graphics.Texture object at 0x7fe7e04c5ac8>, 'color': array([1, 1, 1])}
14:14:50|gym-duckietown|simulator.py:1250|_valid_pose(): Invalid pose. Collision free: True On drivable area: False
14:14:50|gym-duckietown|simulator.py:1251|_valid_pose(): safety_factor: 1.3
14:14:50|gym-duckietown|simulator.py:1252|_valid_pose(): pos: [4.0873995 0.        1.9726338]
14:14:50|gym-duckietown|simulat

14:14:50|gym-duckietown|simulator.py:1250|_valid_pose(): Invalid pose. Collision free: True On drivable area: False
14:14:50|gym-duckietown|simulator.py:1251|_valid_pose(): safety_factor: 1.3
14:14:50|gym-duckietown|simulator.py:1252|_valid_pose(): pos: [3.57292165 0.         1.88314807]
14:14:50|gym-duckietown|simulator.py:1253|_valid_pose(): l_pos: [3.48172154 0.         1.84866924]
14:14:50|gym-duckietown|simulator.py:1254|_valid_pose(): r_pos: [3.66412176 0.         1.91762689]
14:14:50|gym-duckietown|simulator.py:1255|_valid_pose(): f_pos: [3.61429624 0.         1.77370793]
14:14:50|gym-duckietown|simulator.py:1140|_drivable_pos(): [3.50690495 0.         2.23654429] corresponds to tile at (5, 3) which is not drivable: {'coords': (5, 3), 'kind': 'floor', 'angle': 0, 'drivable': False, 'texture': <simulation.src.gym_duckietown.graphics.Texture object at 0x7fe7e04c5ac8>, 'color': array([1, 1, 1])}
14:14:50|gym-duckietown|simulator.py:1250|_valid_pose(): Invalid pose. Collision free: 

14:14:50|gym-duckietown|simulator.py:1255|_valid_pose(): f_pos: [3.50609039 0.         2.05544313]
14:14:50|gym-duckietown|simulator.py:1140|_drivable_pos(): [4.12972415 0.         2.27350789] corresponds to tile at (7, 3) which is not drivable: {'coords': (7, 3), 'kind': 'floor', 'angle': 0, 'drivable': False, 'texture': <simulation.src.gym_duckietown.graphics.Texture object at 0x7fe7e04c5ac8>, 'color': array([1, 1, 1])}
14:14:50|gym-duckietown|simulator.py:1250|_valid_pose(): Invalid pose. Collision free: True On drivable area: False
14:14:50|gym-duckietown|simulator.py:1251|_valid_pose(): safety_factor: 1.3
14:14:50|gym-duckietown|simulator.py:1252|_valid_pose(): pos: [4.022444   0.         2.32019802]
14:14:50|gym-duckietown|simulator.py:1253|_valid_pose(): l_pos: [3.98353555 0.         2.23079789]
14:14:50|gym-duckietown|simulator.py:1254|_valid_pose(): r_pos: [4.06135244 0.         2.40959815]
14:14:50|gym-duckietown|simulator.py:1255|_valid_pose(): f_pos: [4.12972415 0.         

14:14:58|gym-duckietown|simulator.py:1250|_valid_pose(): Invalid pose. Collision free: True On drivable area: False
14:14:58|gym-duckietown|simulator.py:1251|_valid_pose(): safety_factor: 1.3
14:14:58|gym-duckietown|simulator.py:1252|_valid_pose(): pos: [2.38071712 0.         2.71640816]
14:14:58|gym-duckietown|simulator.py:1253|_valid_pose(): l_pos: [2.28873639 0.         2.68406941]
14:14:58|gym-duckietown|simulator.py:1254|_valid_pose(): r_pos: [2.47269785 0.         2.74874692]
14:14:58|gym-duckietown|simulator.py:1255|_valid_pose(): f_pos: [2.41952363 0.         2.60603129]
14:14:58|gym-duckietown|simulator.py:559|reset(): Starting at [2.64153703 0.         2.88468928] 4.836049502872963



Done!



In [50]:
view_results_ipython(local_env)

**<font color='red'>Question 2:</font> When you visualize the results, what are two major issues? Play with the expert's code and the execution code above, and list five changes that you tried, as well as their _qualitative_ effects on performance (i.e cover the most distance). DO NOT RESEED THE ENVIRONMENT**

# Defining a Model

While the above expert isn't great, it's a start. What's best is that we now have image `observations` and real-valued `actions` that we can use to train a neural network in Pytorch. Our imitation learner will driver directly from observations, and will be trained with a popular imitation learning loss: Mean Squared Error.

In [63]:
class Model(nn.Module):
    def __init__(self, action_dim, max_action):
        super(Model, self).__init__()

        # TODO: You'll need to change this!
        flat_size = 31968
        
        ###########################################
        # QUESTION 3. What does the next line do? #
        ###########################################
        self.lr = nn.LeakyReLU()
        self.relu = nn.ReLU()
        self.tanh = nn.Tanh()

        self.conv1 = nn.Conv2d(3, 32, 8, stride=2)
        self.conv2 = nn.Conv2d(32, 32, 4, stride=2)

        self.bn1 = nn.BatchNorm2d(32)
        self.bn2 = nn.BatchNorm2d(32)

        self.dropout = nn.Dropout(.3)

        self.lin1 = nn.Linear(flat_size, 200)
        self.lin2 = nn.Linear(200, action_dim)

        self.max_action = max_action

    def forward(self, x):
        x = self.bn1(self.relu(self.conv1(x)))
        x = self.bn2(self.relu(self.conv2(x)))
        x = x.view(x.size(0), -1)  # flatten
        x = self.dropout(x)
        x = self.lr(self.lin1(x))

        x = self.lin2(x)
        x = self.max_action * self.tanh(x)
        
        return x

# Training from the Teacher Data

We can then write our _training loop_ : the piece of code that implements the process of stochastic gradient descent to minimize the loss between our network's predicted actions and those implemented by our expert.

In [70]:
nepochs = 100
batchsize = 10

actions = np.array(actions)
observations = np.array(observations)

model = Model(action_dim=2, max_action=1.)
model.train().to(device)

# weight_decay is L2 regularization, helps avoid overfitting
optimizer = optim.SGD(
    model.parameters(),
    lr=0.005,
    weight_decay=1e-3
)

avg_loss = 0
for epoch in range(nepochs):
    optimizer.zero_grad()

    batch_indices = np.random.randint(0, observations.shape[0], (batchsize))
    obs_batch = torch.from_numpy(observations[batch_indices]).float().to(device)
    act_batch = torch.from_numpy(actions[batch_indices]).float().to(device)

    model_actions = model(obs_batch)

    loss = (model_actions - act_batch).norm(2).mean()
    loss.backward()
    optimizer.step()

    loss = loss.data.item()
    avg_loss = avg_loss * 0.995 + loss * 0.005
    #avg_loss = avg_loss * 0.9 + loss * 0.1
    print('epoch %d, loss=%.3f' % (epoch, avg_loss))

    # Periodically save the trained model
    if epoch % 5 == 0:
        torch.save(model.state_dict(), 'models/imitate.pt')
        
print('\nDone!\n')

epoch 0, loss=0.005
epoch 1, loss=0.022
epoch 2, loss=0.038
epoch 3, loss=0.050
epoch 4, loss=0.058
epoch 5, loss=0.071
epoch 6, loss=0.082
epoch 7, loss=0.089
epoch 8, loss=0.093
epoch 9, loss=0.097
epoch 10, loss=0.102
epoch 11, loss=0.103
epoch 12, loss=0.109
epoch 13, loss=0.112
epoch 14, loss=0.113
epoch 15, loss=0.115
epoch 16, loss=0.119
epoch 17, loss=0.120
epoch 18, loss=0.122
epoch 19, loss=0.123
epoch 20, loss=0.126
epoch 21, loss=0.129
epoch 22, loss=0.130
epoch 23, loss=0.131
epoch 24, loss=0.132
epoch 25, loss=0.134
epoch 26, loss=0.137
epoch 27, loss=0.138
epoch 28, loss=0.140
epoch 29, loss=0.143
epoch 30, loss=0.143
epoch 31, loss=0.144
epoch 32, loss=0.145
epoch 33, loss=0.146
epoch 34, loss=0.148
epoch 35, loss=0.148
epoch 36, loss=0.149
epoch 37, loss=0.150
epoch 38, loss=0.150
epoch 39, loss=0.153
epoch 40, loss=0.154
epoch 41, loss=0.155
epoch 42, loss=0.156
epoch 43, loss=0.158
epoch 44, loss=0.158
epoch 45, loss=0.158
epoch 46, loss=0.159
epoch 47, loss=0.161
ep

**<font color='red'>Question 3:</font> Qualitatively explain at least 2 changes you made to both the expert and network (architecture, hyperparameters, episode lengths, number of training episodes / epochs, etc.) (including partial points if we find that you didn't make changes to any part of our code - hyperparameters, network, etc.)**


**<font color='red'>Question 4:</font> Explain the issues with the imitation learning loop above. Specifically, comment on the loss function and training objective. Explain at least one issue, and propose a way that could help solve the issues you've brought up.**

In [71]:
force_done(local_env)
local_env = launch_env()
local_env = wrap_env(local_env)
local_env = ResizeWrapper(local_env)
local_env = ImgWrapper(local_env)

obs = local_env.reset()

done = False
rewards = []
nsteps = 500
for steps in range(0, nsteps):
    obs = torch.from_numpy(obs).float().to(device).unsqueeze(0)
    action = model(obs)
    action = action.squeeze().data.cpu().numpy()
    obs, reward, done, info = local_env.step(action) 
    rewards.append(reward)
    
    if done:
        local_env.reset()
        print("Reset!")

print(info)
        
local_env.close()


print("\nDone!\n")
    

14:45:03|gym-duckietown|graphics.py:121|create_frame_buffers(): Falling back to non-multisampled frame buffer
14:45:03|gym-duckietown|graphics.py:121|create_frame_buffers(): Falling back to non-multisampled frame buffer
14:45:03|gym-duckietown|simulator.py:578|_load_map(): loading map file "/duckietown/simulation/src/gym_duckietown/maps/loop_empty.yaml"
14:45:04|gym-duckietown|simulator.py:1140|_drivable_pos(): [4.13719561 0.         1.88880899] corresponds to tile at (7, 3) which is not drivable: {'coords': (7, 3), 'kind': 'floor', 'angle': 0, 'drivable': False, 'texture': <simulation.src.gym_duckietown.graphics.Texture object at 0x7fe7e04c5ac8>, 'color': array([1, 1, 1])}
14:45:04|gym-duckietown|simulator.py:1250|_valid_pose(): Invalid pose. Collision free: True On drivable area: False
14:45:04|gym-duckietown|simulator.py:1251|_valid_pose(): safety_factor: 1.3
14:45:04|gym-duckietown|simulator.py:1252|_valid_pose(): pos: [4.0873995 0.        1.9726338]
14:45:04|gym-duckietown|simulat

14:45:04|gym-duckietown|simulator.py:1250|_valid_pose(): Invalid pose. Collision free: True On drivable area: False
14:45:04|gym-duckietown|simulator.py:1251|_valid_pose(): safety_factor: 1.3
14:45:04|gym-duckietown|simulator.py:1252|_valid_pose(): pos: [3.57292165 0.         1.88314807]
14:45:04|gym-duckietown|simulator.py:1253|_valid_pose(): l_pos: [3.48172154 0.         1.84866924]
14:45:04|gym-duckietown|simulator.py:1254|_valid_pose(): r_pos: [3.66412176 0.         1.91762689]
14:45:04|gym-duckietown|simulator.py:1255|_valid_pose(): f_pos: [3.61429624 0.         1.77370793]
14:45:04|gym-duckietown|simulator.py:1140|_drivable_pos(): [3.50690495 0.         2.23654429] corresponds to tile at (5, 3) which is not drivable: {'coords': (5, 3), 'kind': 'floor', 'angle': 0, 'drivable': False, 'texture': <simulation.src.gym_duckietown.graphics.Texture object at 0x7fe7e04c5ac8>, 'color': array([1, 1, 1])}
14:45:04|gym-duckietown|simulator.py:1250|_valid_pose(): Invalid pose. Collision free: 

14:45:04|gym-duckietown|simulator.py:1255|_valid_pose(): f_pos: [3.50609039 0.         2.05544313]
14:45:04|gym-duckietown|simulator.py:1140|_drivable_pos(): [4.12972415 0.         2.27350789] corresponds to tile at (7, 3) which is not drivable: {'coords': (7, 3), 'kind': 'floor', 'angle': 0, 'drivable': False, 'texture': <simulation.src.gym_duckietown.graphics.Texture object at 0x7fe7e04c5ac8>, 'color': array([1, 1, 1])}
14:45:04|gym-duckietown|simulator.py:1250|_valid_pose(): Invalid pose. Collision free: True On drivable area: False
14:45:04|gym-duckietown|simulator.py:1251|_valid_pose(): safety_factor: 1.3
14:45:04|gym-duckietown|simulator.py:1252|_valid_pose(): pos: [4.022444   0.         2.32019802]
14:45:04|gym-duckietown|simulator.py:1253|_valid_pose(): l_pos: [3.98353555 0.         2.23079789]
14:45:04|gym-duckietown|simulator.py:1254|_valid_pose(): r_pos: [4.06135244 0.         2.40959815]
14:45:04|gym-duckietown|simulator.py:1255|_valid_pose(): f_pos: [4.12972415 0.         

14:45:12|gym-duckietown|simulator.py:1250|_valid_pose(): Invalid pose. Collision free: True On drivable area: False
14:45:12|gym-duckietown|simulator.py:1251|_valid_pose(): safety_factor: 1.3
14:45:12|gym-duckietown|simulator.py:1252|_valid_pose(): pos: [2.38071712 0.         2.71640816]
14:45:12|gym-duckietown|simulator.py:1253|_valid_pose(): l_pos: [2.28873639 0.         2.68406941]
14:45:12|gym-duckietown|simulator.py:1254|_valid_pose(): r_pos: [2.47269785 0.         2.74874692]
14:45:12|gym-duckietown|simulator.py:1255|_valid_pose(): f_pos: [2.41952363 0.         2.60603129]
14:45:12|gym-duckietown|simulator.py:559|reset(): Starting at [2.64153703 0.         2.88468928] 4.836049502872963


{'Simulator': {'action': [0.2530126, 0.2044103], 'lane_position': {'dist': -0.16907763265670983, 'dot_dir': 0.9953245070584595, 'angle_deg': -5.5426912846828715, 'angle_rad': -0.09673821233931046}, 'robot_speed': 0.13828060474129547, 'proximity_penalty': 0.0, 'cur_pos': [0.8254223673432901, 0.0, 2.733844457051438], 'cur_angle': 1.667534539134207, 'wheel_velocities': [0.30361512, 0.24529237], 'timestamp': 16.666666666666654, 'tile_coords': [1, 4], 'msg': ''}}

Done!



In [69]:
view_results_ipython(local_env)

**<font color='red'>Question 5:</font> Copy the value of _info_ , after simulating for 500 steps. If your simulation fails earlier, save the results _before_ the failure (i.e. when the simulation returns `done = True`.  DO NOT RESEED THE ENVIRONMENT** 

# A nastier environment

Once your solution is able to pass a curve while staying in the lane, you can try to see what happens if you modify the test environment with respect to the one used to generate the training dataset. 

To do this, create a new environment called *new_environment* by using the **launch_env()** function as above. This time passing the argument *domain_rand=True*. Basically it randomizes the environment. Once you have the new environment, run again the model without retraining. 

Then, visualize the results. 

**<font color='red'>Question 6:</font> Comment the performance of your solution on the new environment, name two reasons that justify the performance.**

In [72]:
# TODO: Run again the agent in the new randomized environment as explained above

new_env = launch_env(domain_rand=True)
new_env = wrap_env(new_env)
new_env = ResizeWrapper(new_env)
new_env = ImgWrapper(new_env)

obs = new_env.reset()

done = False
rewards = []
nsteps = 300
for steps in range(0, nsteps):
    obs = torch.from_numpy(obs).float().to(device).unsqueeze(0)
    action = model(obs)
    action = action.squeeze().data.cpu().numpy()
    obs, reward, done, info = new_env.step(action) 
    rewards.append(reward)
    
    if done:
        new_env.reset()

new_env.close()

print("\nDone!\n")

14:46:24|gym-duckietown|graphics.py:121|create_frame_buffers(): Falling back to non-multisampled frame buffer
14:46:24|gym-duckietown|graphics.py:121|create_frame_buffers(): Falling back to non-multisampled frame buffer
14:46:24|gym-duckietown|simulator.py:578|_load_map(): loading map file "/duckietown/simulation/src/gym_duckietown/maps/loop_empty.yaml"
14:46:24|gym-duckietown|simulator.py:1140|_drivable_pos(): [0.54829264 0.         2.5248345 ] corresponds to tile at (0, 4) which is not drivable: {'coords': (0, 4), 'kind': 'floor', 'angle': 0, 'drivable': False, 'texture': <simulation.src.gym_duckietown.graphics.Texture object at 0x7fe7e04c5ac8>, 'color': array([0.82985124, 1.15541818, 0.90280541])}
14:46:24|gym-duckietown|simulator.py:1250|_valid_pose(): Invalid pose. Collision free: True On drivable area: False
14:46:24|gym-duckietown|simulator.py:1251|_valid_pose(): safety_factor: 1.3
14:46:24|gym-duckietown|simulator.py:1252|_valid_pose(): pos: [0.63698078 0.         2.48432939]
1

14:46:32|gym-duckietown|simulator.py:1253|_valid_pose(): l_pos: [3.97837341 0.         1.30622148]
14:46:32|gym-duckietown|simulator.py:1254|_valid_pose(): r_pos: [4.16387877 0.         1.36632773]
14:46:32|gym-duckietown|simulator.py:1255|_valid_pose(): f_pos: [4.10718984 0.         1.22497139]
14:46:32|gym-duckietown|simulator.py:1140|_drivable_pos(): [3.49738929 0.         1.1729982 ] corresponds to tile at (5, 2) which is not drivable: {'coords': (5, 2), 'kind': 'floor', 'angle': 0, 'drivable': False, 'texture': <simulation.src.gym_duckietown.graphics.Texture object at 0x7fe7e04c5ac8>, 'color': array([0.9986692 , 1.10691105, 1.10118672])}
14:46:32|gym-duckietown|simulator.py:1250|_valid_pose(): Invalid pose. Collision free: True On drivable area: False
14:46:32|gym-duckietown|simulator.py:1251|_valid_pose(): safety_factor: 1.3
14:46:32|gym-duckietown|simulator.py:1252|_valid_pose(): pos: [3.60007159 0.         1.22908159]
14:46:32|gym-duckietown|simulator.py:1253|_valid_pose(): l_p

14:46:32|gym-duckietown|simulator.py:1250|_valid_pose(): Invalid pose. Collision free: True On drivable area: False
14:46:32|gym-duckietown|simulator.py:1251|_valid_pose(): safety_factor: 1.3
14:46:32|gym-duckietown|simulator.py:1252|_valid_pose(): pos: [3.52677835 0.         1.36436963]
14:46:32|gym-duckietown|simulator.py:1253|_valid_pose(): l_pos: [3.43004286 0.         1.37655549]
14:46:32|gym-duckietown|simulator.py:1254|_valid_pose(): r_pos: [3.62351384 0.         1.35218377]
14:46:32|gym-duckietown|simulator.py:1255|_valid_pose(): f_pos: [3.51215531 0.         1.24828704]
14:46:32|gym-duckietown|simulator.py:559|reset(): Starting at [3.81796031 0.         1.42143052] 1.5639376905286442
14:46:44|gym-duckietown|simulator.py:1140|_drivable_pos(): [4.09562489 0.         0.95768508] corresponds to tile at (7, 1) which is not drivable: {'coords': (7, 1), 'kind': 'floor', 'angle': 0, 'drivable': False, 'texture': <simulation.src.gym_duckietown.graphics.Texture object at 0x7fe7e04c5ac8>

14:46:44|gym-duckietown|simulator.py:1251|_valid_pose(): safety_factor: 1.3
14:46:44|gym-duckietown|simulator.py:1252|_valid_pose(): pos: [1.2816309  0.         3.00624749]
14:46:44|gym-duckietown|simulator.py:1253|_valid_pose(): l_pos: [1.29717298 0.         2.90999421]
14:46:44|gym-duckietown|simulator.py:1254|_valid_pose(): r_pos: [1.26608883 0.         3.10250077]
14:46:44|gym-duckietown|simulator.py:1255|_valid_pose(): f_pos: [1.39713484 0.         3.02489799]
14:46:45|gym-duckietown|simulator.py:1140|_drivable_pos(): [1.58219943 0.         3.51408308] corresponds to tile at (2, 6) which is not drivable: {'coords': (2, 6), 'kind': 'floor', 'angle': 0, 'drivable': False, 'texture': <simulation.src.gym_duckietown.graphics.Texture object at 0x7fe7e04c5ac8>, 'color': array([1.06075544, 0.93886513, 0.86810801])}
14:46:45|gym-duckietown|simulator.py:1250|_valid_pose(): Invalid pose. Collision free: True On drivable area: False
14:46:45|gym-duckietown|simulator.py:1251|_valid_pose(): saf

14:46:45|gym-duckietown|simulator.py:1255|_valid_pose(): f_pos: [1.77677848 0.         2.8875558 ]
14:46:45|gym-duckietown|simulator.py:1140|_drivable_pos(): [1.31550457 0.         3.52207227] corresponds to tile at (2, 6) which is not drivable: {'coords': (2, 6), 'kind': 'floor', 'angle': 0, 'drivable': False, 'texture': <simulation.src.gym_duckietown.graphics.Texture object at 0x7fe7e04c5ac8>, 'color': array([1.06075544, 0.93886513, 0.86810801])}
14:46:45|gym-duckietown|simulator.py:1250|_valid_pose(): Invalid pose. Collision free: True On drivable area: False
14:46:45|gym-duckietown|simulator.py:1251|_valid_pose(): safety_factor: 1.3
14:46:45|gym-duckietown|simulator.py:1252|_valid_pose(): pos: [1.3011635  0.         3.42563274]
14:46:45|gym-duckietown|simulator.py:1253|_valid_pose(): l_pos: [1.28682243 0.         3.3291932 ]
14:46:45|gym-duckietown|simulator.py:1254|_valid_pose(): r_pos: [1.31550457 0.         3.52207227]
14:46:45|gym-duckietown|simulator.py:1255|_valid_pose(): f_p


Done!



In [73]:
# TODO: visualize the results
view_results_ipython(new_env)